In [6]:
pip install transformers

In [9]:
from datasets import load_dataset
import random

In [7]:
import transformers

In [35]:
import pandas as pd

In [23]:
import shap

In [25]:
# IMDB veri setini yükle
dataset = load_dataset("imdb", split="train")

# 20 rastgele metin seç
random.seed(42)
sample_texts = random.sample(list(dataset), 20)

# Metin ve etiketleri ayrı ayır
texts = [item['text'] for item in sample_texts]
labels = [item['label'] for item in sample_texts]

In [36]:
data = pd.DataFrame({
    "text": [item['text'] for item in sample_texts],
    "emotion": [item['label'] for item in sample_texts]
})



In [8]:
from transformers import DistilBertTokenizerFast, DistilBertForSequenceClassification

# Tokenizer ve modeli indirin
tokenizer = DistilBertTokenizerFast.from_pretrained("distilbert-base-uncased")
model = DistilBertForSequenceClassification.from_pretrained("distilbert-base-uncased-finetuned-sst-2-english")

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


tokenizer_config.json:   0%|          | 0.00/48.0 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/232k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/466k [00:00<?, ?B/s]

config.json:   0%|          | 0.00/483 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/629 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/268M [00:00<?, ?B/s]

In [26]:
pip install torch

In [28]:
# build a pipeline object to do predictions
pred = transformers.pipeline(
    "text-classification",
    model=model,
    tokenizer=tokenizer,
    device=-1,  # CPU
    return_all_scores=True,
)

/usr/local/lib/python3.10/dist-packages/transformers/pipelines/text_classification.py:106: UserWarning: `return_all_scores` is now deprecated,  if want a similar functionality use `top_k=None` instead of `return_all_scores=True` or `top_k=1` instead of `return_all_scores=False`.
  warnings.warn(


In [29]:
explainer = shap.Explainer(pred)

In [37]:
shap_values = explainer(data["text"][:3])

  0%|          | 0/498 [00:00<?, ?it/s]

PartitionExplainer explainer:  33%|███▎      | 1/3 [00:00<?, ?it/s]

  0%|          | 0/498 [00:00<?, ?it/s]

PartitionExplainer explainer: 100%|██████████| 3/3 [07:55<00:00, 100.37s/it]

  0%|          | 0/498 [00:00<?, ?it/s]

PartitionExplainer explainer: 4it [09:24, 188.29s/it]


In [58]:


# SHAP grafiklerini çizme
shap.plots.text(shap_values[0])  # İlk metin
shap.plots.text(shap_values[1])

In [38]:
shap.plots.text(shap_values)

In [50]:
print(shap_values.output_names)

['NEGATIVE', 'POSITIVE']


In [52]:
POSITIVE_index = shap_values.output_names.index("POSITIVE")  # "anger" isminin indeksini al
shap.plots.text(shap_values[:, :,POSITIVE_index])

In [42]:
logit_explainer = shap.Explainer(shap.models.TransformersPipeline(pred, rescale_to_logits=True))

logit_shap_values = logit_explainer(data["text"][:3])
shap.plots.text(logit_shap_values)

  0%|          | 0/498 [00:00<?, ?it/s]

PartitionExplainer explainer:  33%|███▎      | 1/3 [00:00<?, ?it/s]

  0%|          | 0/498 [00:00<?, ?it/s]

PartitionExplainer explainer: 100%|██████████| 3/3 [08:20<00:00, 107.56s/it]

  0%|          | 0/498 [00:00<?, ?it/s]

PartitionExplainer explainer: 4it [09:52, 197.40s/it]


In [51]:
NEGATIVE_index = shap_values.output_names.index("NEGATIVE")  # "anger" isminin indeksini al
shap.plots.text(shap_values[:, :, NEGATIVE_index])

In [53]:
import torch

ValueError: text input must be of type `str` (single example), `List[str]` (batch or single pretokenized example) or `List[List[str]]` (batch of pretokenized examples).